# TRAINING I3W


# A) Create Envorinment, Vehicles etc

### General Parameter

In [1]:
# Define horizon as a variable to ensure consistent use across notebook (length of one rollout)
HORIZON=500

# name of the experiment
experiment_name = "IntersectionExample"

# scenario class
import flow.scenarios as scenarios
print("Available scenarios:")
print(scenarios.__all__)
scenario_name = "IntersectionTWScenario"

# environment class
import flow.multiagent_envs as flowenvs
print("\nAvailable environments:")
print(flowenvs.__all__)
env_name = "MultiAgentIntersectionEnv"

Available scenarios:
['Scenario', 'BayBridgeScenario', 'BayBridgeTollScenario', 'BottleneckScenario', 'Figure8Scenario', 'SimpleGridScenario', 'HighwayScenario', 'LoopScenario', 'MergeScenario', 'TwoLoopsOneMergingScenario', 'MultiLoopScenario', 'IntersectionScenarioTW']

Available environments:
['MultiEnv', 'MultiAgentAccelEnv', 'MultiWaveAttenuationPOEnv', 'MultiAgentIntersectionEnv', 'MultiAgentTeamSpiritIntersectionEnv']


### Net Parameter

In [2]:
from flow.core.params import NetParams
from flow.scenarios.intersection import ADDITIONAL_NET_PARAMS

additionalNetParams = {
            "edge_length": 40,
            "lanes": 1,
            "speed_limit": 30
        }

net_params = NetParams( no_internal_links=False,                  #default: True   !! damit Kreuzungen nicht überspr. werden
                        inflows=None,                             #default: None
                        osm_path=None,                            #default: None
                        netfile=None,                             #default: None
                        additional_params=additionalNetParams     #default: None   !!
                      )

### InitialConfig Parameter

In [3]:
from flow.core.params import InitialConfig

initial_config = InitialConfig( shuffle=True,                            #default: False         !!
                                spacing="custom",                        #default: "uniform"     !!
                                min_gap=10,                              #default: 0
                                perturbation=29.99,                      #default: 0.0            !!        
                                x0=0,                                    #default: 0
                                bunching=0,                              #default: 0
                                lanes_distribution=float("inf"),         #default: float("inf")
                                edges_distribution="all",                #default: "all"
                                additional_params=None )                 #default: None

### SUMO Parameter

In [4]:
from flow.core.params import SumoParams

sumo_params = SumoParams( port = None,                  #default: None
                          sim_step=0.1,                 #default: 0.1
                          emission_path=None,           #default: None
                          lateral_resolution=None,      #default: None
                          no_step_log=True,             #default: True
                          render=False,                 #default: False
                          save_render=False,            #default: False
                          sight_radius=25,              #default: 25
                          show_radius=False,            #default: False
                          pxpm=2,                       #default: 2
                          overtake_right=False,         #default: False    
                          seed=None,                    #default: None
                          restart_instance=False,       #default: False
                          print_warnings=True,          #default: True
                          teleport_time=-1,             #default: -1
                          num_clients=1,                #default: 1
                          sumo_binary=None )            #default: None

### Environment Parameter

In [5]:
from flow.core.params import EnvParams

additionalEnvParams = {
        # maximum acceleration of autonomous vehicles
        "max_accel": 3,
        # maximum deceleration of autonomous vehicles
        "max_decel": 3,
        "target_velocity": 30
    }

env_params = EnvParams( additional_params=additionalEnvParams, #default: None    !!
                        horizon=HORIZON,                       #default: 500     !!
                        warmup_steps=0,                        #default: 0       
                        sims_per_step=1,                       #default: 1
                        evaluate=False )                       #default: False

### Vehicles Parameter

In [6]:
from flow.core.params import VehicleParams

# import vehicles dynamics models
#from flow.controllers import SumoCarFollowingController
from flow.controllers import ContinuousRouter
#from flow.controllers.lane_change_controllers import SumoLaneChangeController
from flow.controllers.lane_change_controllers import StaticLaneChanger
from flow.controllers import RLController
from flow.core.params import SumoLaneChangeParams
from flow.core.params import SumoCarFollowingParams
from random import *

vehicles = VehicleParams()

#### Add RL-Agent controlled vehicles 

In [7]:
# car following parameters, default: None
cf_parameter = SumoCarFollowingParams(
                speed_mode="aggressive")
# lane change parameters, default: None
lc_parameter =  None

vehicles.add( # name of the vehicle
                veh_id = "rl",
              # acceleration controller, default: (SumoCarFollowingController, {})
                acceleration_controller=(RLController, {}),
              # lane_change_controller, default: (SumoLaneChangeController, {})
                lane_change_controller=(StaticLaneChanger,{}),
              # routing controller, default: None
                routing_controller=(ContinuousRouter, {}),
              # initial speed, default: 0
                initial_speed=0,
              # number of vehicles, default: 1 
                num_vehicles=2,
                
                car_following_params=cf_parameter
              # speed mode, default: "right_of_way"
                #speed_mode="aggressive",
              # lane change mode, default: "no_lat_collide"
                #lane_change_mode="aggressive", 
              # car following parameter, default: None
                #sumo_car_following_params=cf_parameter,
              # lane change parameter, default: None
                #sumo_lc_params=lc_parameter
)

### Flow Parameter

In [8]:
# Creating flow_params. Make sure the dictionary keys are as specified. 
flow_params = dict( # name of the experiment
                      exp_tag=experiment_name,
                    # name of the flow environment the experiment is running on
                      env_name=env_name,
                    # name of the scenario class the experiment uses
                      scenario=scenario_name,
                    # simulator that is used by the experiment
                      simulator='traci',
                    # sumo-related parameters (see flow.core.params.SumoParams)
                      sim=sumo_params,
                    # environment related parameters (see flow.core.params.EnvParams)
                      env=env_params,
                    # network-related parameters (see flow.core.params.NetParams and
                    # the scenario's documentation or ADDITIONAL_NET_PARAMS component)
                      net=net_params,
                    # vehicles to be placed in the network at the start of a rollout 
                    # (see flow.core.vehicles.Vehicles)
                      veh=vehicles,
                   # (optional) parameters affecting the positioning of vehicles upon 
                   # initialization/reset (see flow.core.params.InitialConfig)
                      initial=initial_config
                )

# B) Training

In [9]:
import json

import ray
try:
    from ray.rllib.agents.agent import get_agent_class
except ImportError:
    from ray.rllib.agents.registry import get_agent_class
from ray.tune import run_experiments
from ray.tune.registry import register_env

from flow.utils.registry import make_create_env
from flow.utils.rllib import FlowParamsEncoder

from ray import tune
from ray.rllib.agents.ppo.ppo_policy_graph import PPOPolicyGraph

In [10]:
# number of parallel workers
N_CPUS = 2
# number of rollouts per training iteration
N_ROLLOUTS = 20

ray.init(redirect_output=True, num_cpus=N_CPUS+1)

Process STDOUT and STDERR is being redirected to /tmp/ray/session_2019-03-15_19-46-27_6072/logs.
Waiting for redis server at 127.0.0.1:10965 to respond...
Waiting for redis server at 127.0.0.1:25163 to respond...
Starting the Plasma object store with 6.554658406 GB memory using /dev/shm.

View the web UI at http://localhost:8889/notebooks/ray_ui.ipynb?token=1e041811bcf829f6ccbd0bd889d94173ae35b399dc0d81bc



{'node_ip_address': '192.168.2.102',
 'object_store_addresses': ['/tmp/ray/session_2019-03-15_19-46-27_6072/sockets/plasma_store'],
 'raylet_socket_names': ['/tmp/ray/session_2019-03-15_19-46-27_6072/sockets/raylet'],
 'redis_address': '192.168.2.102:10965',
 'webui_url': 'http://localhost:8889/notebooks/ray_ui.ipynb?token=1e041811bcf829f6ccbd0bd889d94173ae35b399dc0d81bc'}

In [11]:
def executeTraining():
    
    # The algorithm or model to train. This may refer to "
    #      "the name of a built-on algorithm (e.g. RLLib's DQN "
    #      "or PPO), or a user-defined trainable function or "
    #      "class registered in the tune registry.")
    alg_run = "PPO"

    agent_cls = get_agent_class(alg_run)
    config = agent_cls._default_config.copy()
    config["num_workers"] = N_CPUS  # number of parallel workers
    config["train_batch_size"] = HORIZON * N_ROLLOUTS  # batch size
    config["gamma"] = 0.999  # discount rate
    config["model"].update({"fcnet_hiddens": [64, 32]})  # size of hidden layers in network
    config["use_gae"] = True  # using generalized advantage estimation
    config["lambda"] = 0.97  
    #config["sgd_minibatch_size"] = min(16 * 1024, config["train_batch_size"])  # stochastic gradient descent
    #config["sample_batch_size"] = config["train_batch_size"]/config["num_workers"] # 200 default, trotzdem zu hoch?
    config["kl_target"] = 0.02  # target KL divergence
    config["num_sgd_iter"] = 10  # number of SGD iterations
    config["horizon"] = HORIZON  # rollout horizon

    # save the flow params for replay
    flow_json = json.dumps(flow_params, cls=FlowParamsEncoder, sort_keys=True,
                           indent=4)  # generating a string version of flow_params
    config['env_config']['flow_params'] = flow_json  # adding the flow_params to config dict
    config['env_config']['run'] = alg_run

    # Call the utility function make_create_env to be able to 
    # register the Flow env for this experiment
    create_env, gym_name = make_create_env(params=flow_params, version=0)

    # Register as rllib env with Gym
    register_env(gym_name, create_env)
    
    # multi agent policy mapping
    test_env = create_env()
    obs_space = test_env.observation_space
    act_space = test_env.action_space

    def gen_policy():
        return (PPOPolicyGraph, obs_space, act_space, {})

    # Setup PG with an ensemble of `num_policies` different policy graphs
    policy_graphs = {'rl_0': gen_policy(), 'rl_1': gen_policy()}
    
    def policy_mapping_fn(agent_id):
        return agent_id

    config.update({
            'multiagent': {
                'policy_graphs': policy_graphs,
                'policy_mapping_fn': tune.function(policy_mapping_fn)
            }
        })
    
    trials = run_experiments({
        flow_params["exp_tag"]: {
            "run": alg_run,  # RL algorithm to run
            "env": gym_name,  # environment name generated earlier
            "config": {  # configuration params (must match "run" value)
                **config
            },
            "checkpoint_freq": 1,  # number of iterations between checkpoints
            "max_failures": 999,
            "stop": {  # stopping conditions
                "training_iteration": 250,  # number of iterations to stop after
            },
        },
    })

In [12]:
executeTraining()

 Starting SUMO on port 35983
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 2.6/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-15_19-46-30g0u_vvol -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 2.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



14.185246391238888
20.975612210853335


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_19-47-25
  done: false
  episode_len_mean: 444.0952380952381
  episode_reward_max: 222.678072652914
  episode_reward_mean: 44.649078989591274
  episode_reward_min: -150.1624173850891
  episodes_this_iter: 21
  episodes_total: 21
  experiment_id: 63596cf8d9ad463ca16636d281b94ee1
  hostname: Gandalf
  info:
    grad_time_ms: 4278.209
    load_time_ms: 148.835
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4204784631729126
      kl: 0.0006464617908932269
      policy_loss: -0.001489831367507577
      total_loss: 125.28028869628906
      vf_explained_var: 0.040251243859529495
      vf_loss: 125.28165435791016
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4194120168685913
      kl: 0.0007001225021667778
      policy_loss: -0.000922587234

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 3.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=6120], 120 s, 5 iter, 50000 ts, 102 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_19-49-24
  done: false
  episode_len_mean: 422.51
  episode_reward_max: 320.92394146143164
  episode_reward_mean: 127.84448235504853
  episode_reward_min: -164.6448944023465
  episodes_this_iter: 27
  episodes_total: 138
  experiment_id: 63596cf8d9ad463ca16636d281b94ee1
  hostname: Gandalf
  info:
    grad_time_ms: 3360.487
    load_time_ms: 27.139
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.012500000186264515
      cur_lr: 4.999999873689376e-05
      entropy: 1.4370638132095337
      kl: 0.01881728507578373
      policy_loss: -0.004027616698294878
      total_loss

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 3.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=6120], 238 s, 10 iter, 100000 ts, 175 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_19-51-21
  done: false
  episode_len_mean: 248.56
  episode_reward_max: 336.25555493786123
  episode_reward_mean: 157.23802503195415
  episode_reward_min: -163.62544917168447
  episodes_this_iter: 42
  episodes_total: 329
  experiment_id: 63596cf8d9ad463ca16636d281b94ee1
  hostname: Gandalf
  info:
    grad_time_ms: 3167.169
    load_time_ms: 2.743
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.0007812500116415322
      cur_lr: 4.999999873689376e-05
      entropy: 1.4655736684799194
      kl: 0.00417287228628993
      policy_loss: -0.0023978312965482473
      tota

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=6120], 5368 s, 230 iter, 2300000 ts, 338 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_21-17-01
  done: false
  episode_len_mean: 132.83
  episode_reward_max: 376.0079025967342
  episode_reward_mean: 336.09442573225505
  episode_reward_min: 303.329654710816
  episodes_this_iter: 75
  episodes_total: 16764
  experiment_id: 63596cf8d9ad463ca16636d281b94ee1
  hostname: Gandalf
  info:
    grad_time_ms: 3053.698
    load_time_ms: 2.38
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 2.4504918779991314e-24
      cur_lr: 4.999999873689376e-05
      entropy: 0.1983441561460495
      kl: 0.4503346383571625
      policy_loss: 0.0035076458007097244
      tot

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=6120], 5484 s, 235 iter, 2350000 ts, 335 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_21-18-57
  done: false
  episode_len_mean: 134.11
  episode_reward_max: 377.59590564972484
  episode_reward_mean: 337.31836896015227
  episode_reward_min: 300.8485046741618
  episodes_this_iter: 75
  episodes_total: 17141
  experiment_id: 63596cf8d9ad463ca16636d281b94ee1
  hostname: Gandalf
  info:
    grad_time_ms: 3054.978
    load_time_ms: 2.56
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 3.675737619783471e-24
      cur_lr: 4.999999873689376e-05
      entropy: 0.12725260853767395
      kl: 0.01436846237629652
      policy_loss: 0.0015510079683735967
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=6120], 5600 s, 240 iter, 2400000 ts, 337 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_21-20-53
  done: false
  episode_len_mean: 133.35
  episode_reward_max: 375.65775034075926
  episode_reward_mean: 338.2878251784064
  episode_reward_min: 300.87224803569507
  episodes_this_iter: 74
  episodes_total: 17518
  experiment_id: 63596cf8d9ad463ca16636d281b94ee1
  hostname: Gandalf
  info:
    grad_time_ms: 3057.658
    load_time_ms: 2.419
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 3.675737619783471e-24
      cur_lr: 4.999999873689376e-05
      entropy: 0.1142442375421524
      kl: 0.013013147749006748
      policy_loss: 0.0007367464131675661
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=6120], 5714 s, 245 iter, 2450000 ts, 340 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_21-22-48
  done: false
  episode_len_mean: 131.37
  episode_reward_max: 381.64288893959696
  episode_reward_mean: 339.51939884282785
  episode_reward_min: 295.70689529911033
  episodes_this_iter: 76
  episodes_total: 17893
  experiment_id: 63596cf8d9ad463ca16636d281b94ee1
  hostname: Gandalf
  info:
    grad_time_ms: 3061.917
    load_time_ms: 2.422
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 3.675737619783471e-24
      cur_lr: 4.999999873689376e-05
      entropy: 0.018014317378401756
      kl: 0.01143646240234375
      policy_loss: -0.0014840251533314586
  

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=6120], 5830 s, 250 iter, 2500000 ts, 340 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=6120], 5830 s, 250 iter, 2500000 ts, 340 rew



In [13]:
executeTraining()

 Starting SUMO on port 43023
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 3.5/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-15_21-24-22fzs0dk1f -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 3.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



12.259954930914837
18.211412982384548


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_21-25-19
  done: false
  episode_len_mean: 469.15
  episode_reward_max: 233.25595572584197
  episode_reward_mean: 45.87050406939879
  episode_reward_min: -145.51127729836082
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: 3b01ae105e764e23bbe0124f66bb6454
  hostname: Gandalf
  info:
    grad_time_ms: 4174.203
    load_time_ms: 142.568
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4204384088516235
      kl: 0.000547407369595021
      policy_loss: -0.0002819827350322157
      total_loss: 95.99311065673828
      vf_explained_var: 0.010727101005613804
      vf_loss: 95.9932861328125
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4141510725021362
      kl: 0.0012733839685097337
      policy_loss: -0.002084715524688363
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7461], 117 s, 5 iter, 50000 ts, 55.8 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_21-27-15
  done: false
  episode_len_mean: 412.18
  episode_reward_max: 312.4888142283766
  episode_reward_mean: 61.24008140214944
  episode_reward_min: -166.35666841719097
  episodes_this_iter: 24
  episodes_total: 139
  experiment_id: 3b01ae105e764e23bbe0124f66bb6454
  hostname: Gandalf
  info:
    grad_time_ms: 3380.001
    load_time_ms: 25.709
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4106189012527466
      kl: 0.003628503531217575
      policy_loss: -0.0017596714897081256
      total_l

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7461], 233 s, 10 iter, 100000 ts, 169 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_21-29-11
  done: false
  episode_len_mean: 345.49
  episode_reward_max: 383.30460544980144
  episode_reward_mean: 179.1155746675401
  episode_reward_min: -165.5313706812177
  episodes_this_iter: 33
  episodes_total: 276
  experiment_id: 3b01ae105e764e23bbe0124f66bb6454
  hostname: Gandalf
  info:
    grad_time_ms: 3214.233
    load_time_ms: 2.33
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.0003906250058207661
      cur_lr: 4.999999873689376e-05
      entropy: 1.4065637588500977
      kl: 0.004592257551848888
      policy_loss: -0.0021631610579788685
      total_

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7461], 5341 s, 230 iter, 2300000 ts, 215 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_22-54-30
  done: false
  episode_len_mean: 107.07
  episode_reward_max: 387.04390283114094
  episode_reward_mean: 194.47776723951586
  episode_reward_min: -164.60555063527147
  episodes_this_iter: 91
  episodes_total: 17823
  experiment_id: 3b01ae105e764e23bbe0124f66bb6454
  hostname: Gandalf
  info:
    grad_time_ms: 3139.916
    load_time_ms: 2.327
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.4826791286468506
      kl: 0.027690110728144646
      policy_loss: -0.000799387285951525
      total_loss: 886

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7461], 5458 s, 235 iter, 2350000 ts, 179 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_22-56-26
  done: false
  episode_len_mean: 103.37
  episode_reward_max: 392.33766690789196
  episode_reward_mean: 178.87855835259379
  episode_reward_min: -168.32256515109964
  episodes_this_iter: 97
  episodes_total: 18295
  experiment_id: 3b01ae105e764e23bbe0124f66bb6454
  hostname: Gandalf
  info:
    grad_time_ms: 3129.453
    load_time_ms: 2.315
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.29651811718940735
      kl: 0.014863050542771816
      policy_loss: -0.0001721356820780784
      total_loss: 1

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7461], 5574 s, 240 iter, 2400000 ts, 174 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_22-58-23
  done: false
  episode_len_mean: 102.06
  episode_reward_max: 395.73790529901345
  episode_reward_mean: 174.33661404435682
  episode_reward_min: -162.7019110153013
  episodes_this_iter: 99
  episodes_total: 18759
  experiment_id: 3b01ae105e764e23bbe0124f66bb6454
  hostname: Gandalf
  info:
    grad_time_ms: 3137.246
    load_time_ms: 2.398
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.34160444140434265
      kl: 0.015673520043492317
      policy_loss: 0.00010449802357470617
      total_loss: 10

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7461], 5690 s, 245 iter, 2450000 ts, 180 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_23-00-20
  done: false
  episode_len_mean: 107.72
  episode_reward_max: 380.0780686264396
  episode_reward_mean: 215.46463808784833
  episode_reward_min: -167.963295128083
  episodes_this_iter: 92
  episodes_total: 19234
  experiment_id: 3b01ae105e764e23bbe0124f66bb6454
  hostname: Gandalf
  info:
    grad_time_ms: 3120.016
    load_time_ms: 2.484
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.188462495803833
      kl: 0.012412231415510178
      policy_loss: -9.230127761838958e-05
      total_loss: 818.14

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=7461], 5808 s, 250 iter, 2500000 ts, 219 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=7461], 5808 s, 250 iter, 2500000 ts, 219 rew



In [14]:
executeTraining()

 Starting SUMO on port 55481
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.7/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-15_23-01-55in0lfhts -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 4.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



7.570610352052126
7.44379132756061


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_23-02-54
  done: false
  episode_len_mean: 498.65
  episode_reward_max: 170.47475611806004
  episode_reward_mean: 87.70432500911178
  episode_reward_min: -119.30654216352495
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: 9b970809237441b9a50eed3b1415f24a
  hostname: Gandalf
  info:
    grad_time_ms: 4084.608
    load_time_ms: 142.385
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4246633052825928
      kl: 0.001074183383025229
      policy_loss: -0.0021634234581142664
      total_loss: 22.524871826171875
      vf_explained_var: 0.17586717009544373
      vf_loss: 22.526817321777344
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4232540130615234
      kl: 0.0012878070119768381
      policy_loss: -0.0021028874907642603
  

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7521], 116 s, 5 iter, 50000 ts, 142 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_23-04-48
  done: false
  episode_len_mean: 359.09
  episode_reward_max: 326.06584826141716
  episode_reward_mean: 154.8339446892749
  episode_reward_min: -151.84461367284308
  episodes_this_iter: 32
  episodes_total: 150
  experiment_id: 9b970809237441b9a50eed3b1415f24a
  hostname: Gandalf
  info:
    grad_time_ms: 3267.225
    load_time_ms: 25.741
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.3979257345199585
      kl: 0.0054590436629951
      policy_loss: -0.0032013137824833393
      total_los

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7521], 232 s, 10 iter, 100000 ts, 174 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-15_23-06-45
  done: false
  episode_len_mean: 252.28
  episode_reward_max: 350.59919410284596
  episode_reward_mean: 187.93934713895578
  episode_reward_min: -164.57936496086586
  episodes_this_iter: 40
  episodes_total: 330
  experiment_id: 9b970809237441b9a50eed3b1415f24a
  hostname: Gandalf
  info:
    grad_time_ms: 3114.317
    load_time_ms: 2.393
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.3838242292404175
      kl: 0.0072004892863333225
      policy_loss: -0.0033651250414550304
      t

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7521], 5310 s, 230 iter, 2300000 ts, 344 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_00-31-33
  done: false
  episode_len_mean: 134.66
  episode_reward_max: 390.577757421024
  episode_reward_mean: 344.56615113915416
  episode_reward_min: 293.62940296470833
  episodes_this_iter: 74
  episodes_total: 16345
  experiment_id: 9b970809237441b9a50eed3b1415f24a
  hostname: Gandalf
  info:
    grad_time_ms: 3034.007
    load_time_ms: 2.681
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 5.081338837405425e-20
      cur_lr: 4.999999873689376e-05
      entropy: 0.2217559814453125
      kl: 0.011322722770273685
      policy_loss: -0.0017108035972341895
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7521], 5425 s, 235 iter, 2350000 ts, 341 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_00-33-27
  done: false
  episode_len_mean: 134.59
  episode_reward_max: 396.89290736701
  episode_reward_mean: 345.30241429447807
  episode_reward_min: 150.50929002300256
  episodes_this_iter: 74
  episodes_total: 16718
  experiment_id: 9b970809237441b9a50eed3b1415f24a
  hostname: Gandalf
  info:
    grad_time_ms: 3005.296
    load_time_ms: 2.518
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 7.622009871695271e-20
      cur_lr: 4.999999873689376e-05
      entropy: 0.2368461638689041
      kl: 6.815205097198486
      policy_loss: -0.005711275152862072
      tota

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7521], 5539 s, 240 iter, 2400000 ts, 345 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_00-35-22
  done: false
  episode_len_mean: 137.92
  episode_reward_max: 393.84725847771773
  episode_reward_mean: 344.30323599919
  episode_reward_min: 153.836589030631
  episodes_this_iter: 72
  episodes_total: 17084
  experiment_id: 9b970809237441b9a50eed3b1415f24a
  hostname: Gandalf
  info:
    grad_time_ms: 2995.643
    load_time_ms: 2.657
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 1.1433015130660333e-19
      cur_lr: 4.999999873689376e-05
      entropy: 0.23505260050296783
      kl: 0.15773719549179077
      policy_loss: 0.008639855310320854
      tot

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=7521], 5653 s, 245 iter, 2450000 ts, 349 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_00-37-16
  done: false
  episode_len_mean: 137.12
  episode_reward_max: 395.91621094658973
  episode_reward_mean: 343.8763363077261
  episode_reward_min: -131.81601546986894
  episodes_this_iter: 73
  episodes_total: 17448
  experiment_id: 9b970809237441b9a50eed3b1415f24a
  hostname: Gandalf
  info:
    grad_time_ms: 3011.178
    load_time_ms: 2.626
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 3.8586414272192547e-19
      cur_lr: 4.999999873689376e-05
      entropy: 0.24488331377506256
      kl: 0.02620983123779297
      policy_loss: -0.007303346414119005
   

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=7521], 5767 s, 250 iter, 2500000 ts, 333 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=7521], 5767 s, 250 iter, 2500000 ts, 333 rew



In [15]:
executeTraining()

 Starting SUMO on port 52327
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.8/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-16_00-38-49cd6pa1wc -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 5.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



8.301965510956174
10.710899513891299


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_00-39-26
  done: false
  episode_len_mean: 486.5
  episode_reward_max: 189.42097382279732
  episode_reward_mean: 57.57677621561136
  episode_reward_min: -160.5236817288316
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: f156154b3f66448dbb2a78f4a163419b
  hostname: Gandalf
  info:
    grad_time_ms: 4020.143
    load_time_ms: 141.281
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4184932708740234
      kl: 0.0012693508761003613
      policy_loss: -0.0016403376357629895
      total_loss: 68.26170349121094
      vf_explained_var: 0.01592213287949562
      vf_loss: 68.26306915283203
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4191821813583374
      kl: 0.0013002032646909356
      policy_loss: -0.0016276350943371654
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.2/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=8788], 115 s, 5 iter, 50000 ts, 115 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_00-41-20
  done: false
  episode_len_mean: 416.98
  episode_reward_max: 377.8943891226113
  episode_reward_mean: 116.38375656777349
  episode_reward_min: -164.2774211541708
  episodes_this_iter: 28
  episodes_total: 137
  experiment_id: f156154b3f66448dbb2a78f4a163419b
  hostname: Gandalf
  info:
    grad_time_ms: 3217.456
    load_time_ms: 25.681
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4185805320739746
      kl: 0.001790710142813623
      policy_loss: -0.0019309070194140077
      total_lo

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=8788], 230 s, 10 iter, 100000 ts, 155 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_00-43-15
  done: false
  episode_len_mean: 294.22
  episode_reward_max: 378.01737622420296
  episode_reward_mean: 143.7713342143519
  episode_reward_min: -153.4764137094124
  episodes_this_iter: 38
  episodes_total: 297
  experiment_id: f156154b3f66448dbb2a78f4a163419b
  hostname: Gandalf
  info:
    grad_time_ms: 3077.137
    load_time_ms: 2.478
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.4411182403564453
      kl: 0.000992991030216217
      policy_loss: -0.0004092831222806126
      tota

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=8788], 5317 s, 230 iter, 2300000 ts, 362 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_02-08-13
  done: false
  episode_len_mean: 134.61
  episode_reward_max: 396.857733492003
  episode_reward_mean: 364.34934163399936
  episode_reward_min: 340.7385719458333
  episodes_this_iter: 74
  episodes_total: 16070
  experiment_id: f156154b3f66448dbb2a78f4a163419b
  hostname: Gandalf
  info:
    grad_time_ms: 3011.102
    load_time_ms: 2.457
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.6679245233535767
      kl: 0.006251384038478136
      policy_loss: -0.0012486675987020135
      total_loss: 1.2314

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.2/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=8788], 5433 s, 235 iter, 2350000 ts, 364 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_02-10-09
  done: false
  episode_len_mean: 134.87
  episode_reward_max: 391.1494182137428
  episode_reward_mean: 359.00128006829283
  episode_reward_min: 92.25233004172941
  episodes_this_iter: 74
  episodes_total: 16440
  experiment_id: f156154b3f66448dbb2a78f4a163419b
  hostname: Gandalf
  info:
    grad_time_ms: 3029.559
    load_time_ms: 2.519
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.6543087363243103
      kl: 0.005851191934198141
      policy_loss: -0.0007284085731953382
      total_loss: 26.51

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=8788], 5548 s, 240 iter, 2400000 ts, 364 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_02-12-05
  done: false
  episode_len_mean: 136.03
  episode_reward_max: 395.782715410378
  episode_reward_mean: 364.2073017310555
  episode_reward_min: 336.7010155179608
  episodes_this_iter: 73
  episodes_total: 16809
  experiment_id: f156154b3f66448dbb2a78f4a163419b
  hostname: Gandalf
  info:
    grad_time_ms: 3030.711
    load_time_ms: 2.454
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.6703609824180603
      kl: 0.005755465477705002
      policy_loss: -0.0010495060123503208
      total_loss: 0.86440

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=8788], 5664 s, 245 iter, 2450000 ts, 361 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_02-14-00
  done: false
  episode_len_mean: 136.07
  episode_reward_max: 392.22078949748266
  episode_reward_mean: 367.1118138383986
  episode_reward_min: 340.93321268984704
  episodes_this_iter: 72
  episodes_total: 17175
  experiment_id: f156154b3f66448dbb2a78f4a163419b
  hostname: Gandalf
  info:
    grad_time_ms: 3046.945
    load_time_ms: 2.308
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.6248233318328857
      kl: 0.005697138607501984
      policy_loss: -0.00024427432799711823
      total_loss: 0.7

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=8788], 5778 s, 250 iter, 2500000 ts, 354 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=8788], 5778 s, 250 iter, 2500000 ts, 354 rew



In [16]:
executeTraining()

 Starting SUMO on port 56893
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.1/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-16_02-15-334agdw911 -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 6.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



22.2290626595547
25.98884184658098


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_02-16-31
  done: false
  episode_len_mean: 460.55
  episode_reward_max: 166.96364155438937
  episode_reward_mean: 44.01884152999507
  episode_reward_min: -151.64511966705183
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: 20550ba960844b1bbc91f4a2edf3861d
  hostname: Gandalf
  info:
    grad_time_ms: 4331.902
    load_time_ms: 149.004
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4203226566314697
      kl: 0.000493006722535938
      policy_loss: -0.0008918464300222695
      total_loss: 80.62206268310547
      vf_explained_var: 0.04680429399013519
      vf_loss: 80.62285614013672
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4206947088241577
      kl: 0.000603377993684262
      policy_loss: -0.0005594997783191502
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11531], 116 s, 5 iter, 50000 ts, 65.4 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_02-18-25
  done: false
  episode_len_mean: 441.46
  episode_reward_max: 321.2478104401037
  episode_reward_mean: 101.79668706607197
  episode_reward_min: -159.20335210300462
  episodes_this_iter: 22
  episodes_total: 134
  experiment_id: 20550ba960844b1bbc91f4a2edf3861d
  hostname: Gandalf
  info:
    grad_time_ms: 3387.014
    load_time_ms: 26.858
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4314429759979248
      kl: 0.011563713662326336
      policy_loss: -0.007818739861249924
      total_

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11531], 232 s, 10 iter, 100000 ts, 166 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_02-20-22
  done: false
  episode_len_mean: 245.02
  episode_reward_max: 381.3242796690889
  episode_reward_mean: 166.38846640823874
  episode_reward_min: -155.2345126388563
  episodes_this_iter: 43
  episodes_total: 316
  experiment_id: 20550ba960844b1bbc91f4a2edf3861d
  hostname: Gandalf
  info:
    grad_time_ms: 3199.324
    load_time_ms: 2.58
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.0003906250058207661
      cur_lr: 4.999999873689376e-05
      entropy: 1.392999291419983
      kl: 0.005530933849513531
      policy_loss: -0.0019852377008646727
      total_

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11531], 5323 s, 230 iter, 2300000 ts, 332 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_03-45-23
  done: false
  episode_len_mean: 125.67
  episode_reward_max: 377.7793556804678
  episode_reward_mean: 339.4314998413655
  episode_reward_min: 286.10126500545306
  episodes_this_iter: 79
  episodes_total: 17866
  experiment_id: 20550ba960844b1bbc91f4a2edf3861d
  hostname: Gandalf
  info:
    grad_time_ms: 3061.452
    load_time_ms: 2.832
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 8.354909504317013e-21
      cur_lr: 4.999999873689376e-05
      entropy: 0.20886291563510895
      kl: 0.020088858902454376
      policy_loss: 0.006620900705456734
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11531], 5438 s, 235 iter, 2350000 ts, 339 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_03-47-18
  done: false
  episode_len_mean: 124.42
  episode_reward_max: 379.94471928955875
  episode_reward_mean: 338.7519804387433
  episode_reward_min: 287.5788131837119
  episodes_this_iter: 80
  episodes_total: 18267
  experiment_id: 20550ba960844b1bbc91f4a2edf3861d
  hostname: Gandalf
  info:
    grad_time_ms: 3039.433
    load_time_ms: 2.888
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 1.2532369507133705e-20
      cur_lr: 4.999999873689376e-05
      entropy: 0.21289664506912231
      kl: 0.032457973808050156
      policy_loss: 0.01424045767635107
     

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11531], 5552 s, 240 iter, 2400000 ts, 340 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_03-49-13
  done: false
  episode_len_mean: 123.24
  episode_reward_max: 381.2080905753955
  episode_reward_mean: 340.92213879965135
  episode_reward_min: -142.35295149567924
  episodes_this_iter: 81
  episodes_total: 18670
  experiment_id: 20550ba960844b1bbc91f4a2edf3861d
  hostname: Gandalf
  info:
    grad_time_ms: 3027.06
    load_time_ms: 2.513
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 2.819781806245698e-20
      cur_lr: 4.999999873689376e-05
      entropy: 0.2299434244632721
      kl: 0.03942795842885971
      policy_loss: 0.01615658588707447
      t

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11531], 5667 s, 245 iter, 2450000 ts, 318 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_03-51-08
  done: false
  episode_len_mean: 121.39
  episode_reward_max: 387.315245180397
  episode_reward_mean: 329.8383652322882
  episode_reward_min: -142.50492716659346
  episodes_this_iter: 83
  episodes_total: 19080
  experiment_id: 20550ba960844b1bbc91f4a2edf3861d
  hostname: Gandalf
  info:
    grad_time_ms: 3035.909
    load_time_ms: 2.348
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 1.4275149554255716e-19
      cur_lr: 4.999999873689376e-05
      entropy: 0.17932887375354767
      kl: 15.574384689331055
      policy_loss: 0.035106856375932693
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=11531], 5783 s, 250 iter, 2500000 ts, 306 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=11531], 5783 s, 250 iter, 2500000 ts, 306 rew



In [17]:
executeTraining()

 Starting SUMO on port 51629
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-16_03-52-41zi0ztudu -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



13.158170968597778
1.9637819609747709


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_03-53-41
  done: false
  episode_len_mean: 475.9
  episode_reward_max: 225.10785036774976
  episode_reward_mean: 78.3440425605223
  episode_reward_min: -148.14493811964707
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: 6a538aa2882144288cee4b6caba79e19
  hostname: Gandalf
  info:
    grad_time_ms: 4132.78
    load_time_ms: 143.57
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.417690396308899
      kl: 0.0010189954191446304
      policy_loss: -0.0011139920679852366
      total_loss: 33.6623649597168
      vf_explained_var: 0.12451547384262085
      vf_loss: 33.66328048706055
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4218324422836304
      kl: 0.0006168478867039084
      policy_loss: -0.0025531200226396322
      tot

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11586], 118 s, 5 iter, 50000 ts, 107 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_03-55-36
  done: false
  episode_len_mean: 430.52
  episode_reward_max: 317.76570024224606
  episode_reward_mean: 140.63583570101505
  episode_reward_min: -165.63339430279675
  episodes_this_iter: 26
  episodes_total: 135
  experiment_id: 6a538aa2882144288cee4b6caba79e19
  hostname: Gandalf
  info:
    grad_time_ms: 3301.853
    load_time_ms: 26.025
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4186124801635742
      kl: 0.0048323627561330795
      policy_loss: -0.0027323239482939243
      tota

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.3/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11586], 233 s, 10 iter, 100000 ts, 174 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_03-57-33
  done: false
  episode_len_mean: 233.86
  episode_reward_max: 377.5018249463362
  episode_reward_mean: 183.90883122552256
  episode_reward_min: -162.66275106689613
  episodes_this_iter: 45
  episodes_total: 325
  experiment_id: 6a538aa2882144288cee4b6caba79e19
  hostname: Gandalf
  info:
    grad_time_ms: 3152.842
    load_time_ms: 2.497
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.383658766746521
      kl: 0.005593016743659973
      policy_loss: -0.0016321531729772687
      tot

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11586], 5341 s, 230 iter, 2300000 ts, 293 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_05-22-50
  done: false
  episode_len_mean: 111.99
  episode_reward_max: 371.7718408519683
  episode_reward_mean: 255.3485709355052
  episode_reward_min: -167.69399170979634
  episodes_this_iter: 90
  episodes_total: 18967
  experiment_id: 6a538aa2882144288cee4b6caba79e19
  hostname: Gandalf
  info:
    grad_time_ms: 3060.506
    load_time_ms: 2.602
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.7880701422691345
      kl: 0.007537589408457279
      policy_loss: -0.002633859636262059
      total_loss: 688.

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11586], 5456 s, 235 iter, 2350000 ts, 273 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_05-24-46
  done: false
  episode_len_mean: 113.36
  episode_reward_max: 375.9209805678612
  episode_reward_mean: 266.71009873289256
  episode_reward_min: -164.24981996066606
  episodes_this_iter: 89
  episodes_total: 19404
  experiment_id: 6a538aa2882144288cee4b6caba79e19
  hostname: Gandalf
  info:
    grad_time_ms: 3054.311
    load_time_ms: 2.44
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.6808080077171326
      kl: 0.003304489888250828
      policy_loss: -0.0008041919791139662
      total_loss: 660

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11586], 5571 s, 240 iter, 2400000 ts, 265 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_05-26-41
  done: false
  episode_len_mean: 118.1
  episode_reward_max: 376.880462870923
  episode_reward_mean: 289.4736656412252
  episode_reward_min: -154.00950979327692
  episodes_this_iter: 84
  episodes_total: 19835
  experiment_id: 6a538aa2882144288cee4b6caba79e19
  hostname: Gandalf
  info:
    grad_time_ms: 3042.356
    load_time_ms: 2.467
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.7054092288017273
      kl: 0.007299729622900486
      policy_loss: -0.001733990851789713
      total_loss: 369.55

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=11586], 5686 s, 245 iter, 2450000 ts, 255 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_05-28-37
  done: false
  episode_len_mean: 111.68
  episode_reward_max: 371.73069477292853
  episode_reward_mean: 254.38225396087762
  episode_reward_min: -157.21597439079392
  episodes_this_iter: 90
  episodes_total: 20276
  experiment_id: 6a538aa2882144288cee4b6caba79e19
  hostname: Gandalf
  info:
    grad_time_ms: 3024.776
    load_time_ms: 2.473
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.6447128057479858
      kl: 0.0033414876088500023
      policy_loss: -0.0008293116115964949
      total_loss: 

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=11586], 5802 s, 250 iter, 2500000 ts, 298 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=11586], 5802 s, 250 iter, 2500000 ts, 298 rew



In [18]:
executeTraining()

 Starting SUMO on port 46463
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.2/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-16_05-30-10a4o30o_v -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.2/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



20.90777836676881
3.996570103657498


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_05-30-48
  done: false
  episode_len_mean: 482.3
  episode_reward_max: 224.09629962626445
  episode_reward_mean: 69.05335200408665
  episode_reward_min: -140.18420703767222
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: 5c3ea7354895452d94534bdd12753dcb
  hostname: Gandalf
  info:
    grad_time_ms: 4026.845
    load_time_ms: 141.323
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.422379493713379
      kl: 0.0013371440581977367
      policy_loss: -0.0016553581226617098
      total_loss: 56.40946578979492
      vf_explained_var: 0.08510105311870575
      vf_loss: 56.410850524902344
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4217745065689087
      kl: 0.0005206184578128159
      policy_loss: -0.0007711558137089014
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=12934], 115 s, 5 iter, 50000 ts, 108 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_05-32-41
  done: false
  episode_len_mean: 397.15
  episode_reward_max: 340.90716906926747
  episode_reward_mean: 105.51886156784344
  episode_reward_min: -159.55837165381828
  episodes_this_iter: 29
  episodes_total: 141
  experiment_id: 5c3ea7354895452d94534bdd12753dcb
  hostname: Gandalf
  info:
    grad_time_ms: 3187.537
    load_time_ms: 25.585
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4230505228042603
      kl: 0.0038782779593020678
      policy_loss: -0.0011354110902175307
      tota

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=12934], 228 s, 10 iter, 100000 ts, 201 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_05-34-36
  done: false
  episode_len_mean: 297.44
  episode_reward_max: 366.4736399705221
  episode_reward_mean: 219.6957031327795
  episode_reward_min: -156.60150911419575
  episodes_this_iter: 36
  episodes_total: 299
  experiment_id: 5c3ea7354895452d94534bdd12753dcb
  hostname: Gandalf
  info:
    grad_time_ms: 3025.99
    load_time_ms: 2.481
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.3735164403915405
      kl: 0.007029008585959673
      policy_loss: -0.0017180832801386714
      tota

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=12934], 5312 s, 230 iter, 2300000 ts, 326 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_06-59-29
  done: false
  episode_len_mean: 144.77
  episode_reward_max: 360.2174649336967
  episode_reward_mean: 325.3840945332094
  episode_reward_min: 287.8233718443698
  episodes_this_iter: 70
  episodes_total: 15020
  experiment_id: 5c3ea7354895452d94534bdd12753dcb
  hostname: Gandalf
  info:
    grad_time_ms: 3010.518
    load_time_ms: 2.495
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 3.7421448047508105e-14
      cur_lr: 4.999999873689376e-05
      entropy: 0.0882515236735344
      kl: 0.015604238957166672
      policy_loss: 0.0041585648432374
      to

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=12934], 5426 s, 235 iter, 2350000 ts, 326 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_07-01-23
  done: false
  episode_len_mean: 144.62
  episode_reward_max: 357.37270664796984
  episode_reward_mean: 325.76097749596215
  episode_reward_min: 293.2783893856366
  episodes_this_iter: 70
  episodes_total: 15366
  experiment_id: 5c3ea7354895452d94534bdd12753dcb
  hostname: Gandalf
  info:
    grad_time_ms: 3018.513
    load_time_ms: 2.351
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 5.6132175459393946e-14
      cur_lr: 4.999999873689376e-05
      entropy: 0.040925033390522
      kl: 0.021731244400143623
      policy_loss: 0.0007871999405324459
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=12934], 5540 s, 240 iter, 2400000 ts, 319 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_07-03-17
  done: false
  episode_len_mean: 145.78
  episode_reward_max: 355.6072520330849
  episode_reward_mean: 326.7228894609249
  episode_reward_min: 287.53284267104857
  episodes_this_iter: 69
  episodes_total: 15713
  experiment_id: 5c3ea7354895452d94534bdd12753dcb
  hostname: Gandalf
  info:
    grad_time_ms: 3010.092
    load_time_ms: 2.258
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 4.2099129900479565e-14
      cur_lr: 4.999999873689376e-05
      entropy: 0.09963693469762802
      kl: 0.020767977461218834
      policy_loss: 0.0019173210021108389
   

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=12934], 5654 s, 245 iter, 2450000 ts, 328 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_07-05-11
  done: false
  episode_len_mean: 145.86
  episode_reward_max: 364.09483621535475
  episode_reward_mean: 325.7070780303791
  episode_reward_min: 288.06083823301447
  episodes_this_iter: 68
  episodes_total: 16055
  experiment_id: 5c3ea7354895452d94534bdd12753dcb
  hostname: Gandalf
  info:
    grad_time_ms: 3002.975
    load_time_ms: 2.212
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 4.2099129900479565e-14
      cur_lr: 4.999999873689376e-05
      entropy: 0.04361474886536598
      kl: 0.015627054497599602
      policy_loss: 0.00012752757174894214
 

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=12934], 5768 s, 250 iter, 2500000 ts, 327 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.7/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=12934], 5768 s, 250 iter, 2500000 ts, 327 rew



In [19]:
executeTraining()

 Starting SUMO on port 59043
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.8/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-16_07-06-459ng3s251 -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 7.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



10.957504619834332
17.644324126891608


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_07-07-43
  done: false
  episode_len_mean: 442.8181818181818
  episode_reward_max: 180.19796888057584
  episode_reward_mean: 42.19472211105914
  episode_reward_min: -153.75328963924363
  episodes_this_iter: 22
  episodes_total: 22
  experiment_id: 66dfac4d4bef4417b3614ae78383d242
  hostname: Gandalf
  info:
    grad_time_ms: 4137.981
    load_time_ms: 140.993
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.418033242225647
      kl: 0.000716587295755744
      policy_loss: -0.0011960151605308056
      total_loss: 99.93111419677734
      vf_explained_var: 0.04277541860938072
      vf_loss: 99.93217468261719
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4212207794189453
      kl: 0.000382322003133595
      policy_loss: -0.001716250786557

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15639], 116 s, 5 iter, 50000 ts, 107 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_07-09-37
  done: false
  episode_len_mean: 445.61
  episode_reward_max: 329.09974058977184
  episode_reward_mean: 138.1547633246074
  episode_reward_min: -150.38365234295665
  episodes_this_iter: 25
  episodes_total: 133
  experiment_id: 66dfac4d4bef4417b3614ae78383d242
  hostname: Gandalf
  info:
    grad_time_ms: 3337.813
    load_time_ms: 25.478
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.012500000186264515
      cur_lr: 4.999999873689376e-05
      entropy: 1.3656378984451294
      kl: 0.008572235703468323
      policy_loss: -0.0026705574709922075
      total_l

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15639], 230 s, 10 iter, 100000 ts, 202 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_07-11-31
  done: false
  episode_len_mean: 251.71
  episode_reward_max: 375.39376805737953
  episode_reward_mean: 204.75104735585526
  episode_reward_min: -153.8168149767231
  episodes_this_iter: 42
  episodes_total: 314
  experiment_id: 66dfac4d4bef4417b3614ae78383d242
  hostname: Gandalf
  info:
    grad_time_ms: 3176.665
    load_time_ms: 2.412
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.0003906250058207661
      cur_lr: 4.999999873689376e-05
      entropy: 1.3647626638412476
      kl: 0.00784820131957531
      policy_loss: -0.002342699794098735
      total

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15639], 5350 s, 230 iter, 2300000 ts, 345 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_08-37-02
  done: false
  episode_len_mean: 121.93
  episode_reward_max: 385.9752718130717
  episode_reward_mean: 346.2893963120735
  episode_reward_min: 299.04794700966727
  episodes_this_iter: 82
  episodes_total: 17080
  experiment_id: 66dfac4d4bef4417b3614ae78383d242
  hostname: Gandalf
  info:
    grad_time_ms: 3005.511
    load_time_ms: 2.434
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.016559751704335213
      kl: 0.007875403389334679
      policy_loss: -0.0017023057444021106
      total_loss: 2.

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15639], 5466 s, 235 iter, 2350000 ts, 347 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_08-38-58
  done: false
  episode_len_mean: 122.68
  episode_reward_max: 386.8242485940164
  episode_reward_mean: 346.15518286358883
  episode_reward_min: 307.0859609917647
  episodes_this_iter: 82
  episodes_total: 17489
  experiment_id: 66dfac4d4bef4417b3614ae78383d242
  hostname: Gandalf
  info:
    grad_time_ms: 3023.805
    load_time_ms: 2.369
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: 0.007320705335587263
      kl: 0.010239715687930584
      policy_loss: -0.0024735366459935904
      total_loss: 2.

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15639], 5580 s, 240 iter, 2400000 ts, 340 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_08-40-52
  done: false
  episode_len_mean: 121.46
  episode_reward_max: 384.7843400589058
  episode_reward_mean: 343.7299170377201
  episode_reward_min: 301.6585387362985
  episodes_this_iter: 83
  episodes_total: 17900
  experiment_id: 66dfac4d4bef4417b3614ae78383d242
  hostname: Gandalf
  info:
    grad_time_ms: 3019.354
    load_time_ms: 2.215
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: -0.028535932302474976
      kl: 0.008393562398850918
      policy_loss: -0.0032593633513897657
      total_loss: 2.

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15639], 5695 s, 245 iter, 2450000 ts, 335 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_08-42-48
  done: false
  episode_len_mean: 121.48
  episode_reward_max: 378.3485096863348
  episode_reward_mean: 344.95567852616756
  episode_reward_min: 298.95026460288256
  episodes_this_iter: 82
  episodes_total: 18311
  experiment_id: 66dfac4d4bef4417b3614ae78383d242
  hostname: Gandalf
  info:
    grad_time_ms: 3014.646
    load_time_ms: 2.328
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 0.0
      cur_lr: 4.999999873689376e-05
      entropy: -0.00568760558962822
      kl: 0.012159575708210468
      policy_loss: -0.0026044112164527178
      total_loss: 2

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=15639], 5811 s, 250 iter, 2500000 ts, 335 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=15639], 5811 s, 250 iter, 2500000 ts, 335 rew



In [20]:
executeTraining()

 Starting SUMO on port 38227
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.1/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-16_08-44-23y6gvqxti -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



3.2951957799774645
20.073916229565203


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_08-45-22
  done: false
  episode_len_mean: 493.6
  episode_reward_max: 211.41740660329017
  episode_reward_mean: 102.45080646431802
  episode_reward_min: -141.06065739003904
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: ee4541f6ec54417a81146033521df0f9
  hostname: Gandalf
  info:
    grad_time_ms: 4076.763
    load_time_ms: 140.286
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.426827311515808
      kl: 0.0019523317459970713
      policy_loss: -0.003468233859166503
      total_loss: 28.603544235229492
      vf_explained_var: 0.21481865644454956
      vf_loss: 28.60662078857422
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4209234714508057
      kl: 0.0005891452310606837
      policy_loss: -0.0007949161808937788
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15699], 116 s, 5 iter, 50000 ts, 84.9 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_08-47-17
  done: false
  episode_len_mean: 439.66
  episode_reward_max: 284.50764431840986
  episode_reward_mean: 93.87761829795103
  episode_reward_min: -165.86209647971805
  episodes_this_iter: 23
  episodes_total: 132
  experiment_id: ee4541f6ec54417a81146033521df0f9
  hostname: Gandalf
  info:
    grad_time_ms: 3278.766
    load_time_ms: 25.261
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.012500000186264515
      cur_lr: 4.999999873689376e-05
      entropy: 1.3859541416168213
      kl: 0.003478431608527899
      policy_loss: -0.002000587759539485
      total_l

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15699], 230 s, 10 iter, 100000 ts, 168 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_08-49-11
  done: false
  episode_len_mean: 359.31
  episode_reward_max: 397.3207344507491
  episode_reward_mean: 162.46372780004089
  episode_reward_min: -157.81617602320767
  episodes_this_iter: 31
  episodes_total: 267
  experiment_id: ee4541f6ec54417a81146033521df0f9
  hostname: Gandalf
  info:
    grad_time_ms: 3115.147
    load_time_ms: 2.266
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.0003906250058207661
      cur_lr: 4.999999873689376e-05
      entropy: 1.3661308288574219
      kl: 0.0034161775838583708
      policy_loss: -0.002299199579283595
      tot

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.0/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15699], 5769 s, 230 iter, 2300000 ts, 359 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-21-48
  done: false
  episode_len_mean: 129.63
  episode_reward_max: 394.11483417068746
  episode_reward_mean: 353.9078461986288
  episode_reward_min: -140.9605134460723
  episodes_this_iter: 77
  episodes_total: 15954
  experiment_id: ee4541f6ec54417a81146033521df0f9
  hostname: Gandalf
  info:
    grad_time_ms: 6839.824
    load_time_ms: 3.219
    num_steps_sampled: 2310000
    num_steps_trained: 2310000
    rl_0:
      cur_kl_coeff: 1.9293207136096274e-19
      cur_lr: 4.999999873689376e-05
      entropy: 0.10009374469518661
      kl: 0.5887627005577087
      policy_loss: 0.006110407877713442
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15699], 5913 s, 235 iter, 2350000 ts, 347 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-24-12
  done: false
  episode_len_mean: 127.63
  episode_reward_max: 398.82484790846985
  episode_reward_mean: 344.1224800773756
  episode_reward_min: -148.90430775267575
  episodes_this_iter: 79
  episodes_total: 16342
  experiment_id: ee4541f6ec54417a81146033521df0f9
  hostname: Gandalf
  info:
    grad_time_ms: 4310.732
    load_time_ms: 2.84
    num_steps_sampled: 2360000
    num_steps_trained: 2360000
    rl_0:
      cur_kl_coeff: 9.767189440758234e-19
      cur_lr: 4.999999873689376e-05
      entropy: 0.1337096095085144
      kl: 3.307927370071411
      policy_loss: 0.005632770713418722
      to

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15699], 6095 s, 240 iter, 2400000 ts, 357 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-27-13
  done: false
  episode_len_mean: 128.33
  episode_reward_max: 389.02057549547266
  episode_reward_mean: 362.03374103464057
  episode_reward_min: 333.60280673391196
  episodes_this_iter: 78
  episodes_total: 16731
  experiment_id: ee4541f6ec54417a81146033521df0f9
  hostname: Gandalf
  info:
    grad_time_ms: 4792.924
    load_time_ms: 3.29
    num_steps_sampled: 2410000
    num_steps_trained: 2410000
    rl_0:
      cur_kl_coeff: 4.94463796124854e-18
      cur_lr: 4.999999873689376e-05
      entropy: 0.12173916399478912
      kl: 0.014698967337608337
      policy_loss: 0.0054800985381007195
    

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 10.1/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=15699], 6261 s, 245 iter, 2450000 ts, 362 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-30-12
  done: false
  episode_len_mean: 128.24
  episode_reward_max: 391.9262431436814
  episode_reward_mean: 356.01539623650046
  episode_reward_min: -142.20081201533162
  episodes_this_iter: 78
  episodes_total: 17121
  experiment_id: ee4541f6ec54417a81146033521df0f9
  hostname: Gandalf
  info:
    grad_time_ms: 5011.592
    load_time_ms: 3.437
    num_steps_sampled: 2460000
    num_steps_trained: 2460000
    rl_0:
      cur_kl_coeff: 3.708478160743675e-18
      cur_lr: 4.999999873689376e-05
      entropy: 0.155276820063591
      kl: 28.742816925048828
      policy_loss: 0.028615670278668404
      

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=15699], 6439 s, 250 iter, 2500000 ts, 353 rew

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.8/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
TERMINATED trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	TERMINATED [pid=15699], 6439 s, 250 iter, 2500000 ts, 353 rew



In [ ]:
executeTraining()

 Starting SUMO on port 52631
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB

Created LogSyncer for /home/thorsten/ray_results/IntersectionExample/PPO_MultiAgentIntersectionEnv-v0_0_2019-03-16_10-32-29hed5wc05 -> 
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 8.9/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING



16.434145357006784
14.367219755037919


Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-33-07
  done: false
  episode_len_mean: 489.0
  episode_reward_max: 179.3880309181247
  episode_reward_mean: 86.1190011133148
  episode_reward_min: -151.7486308010638
  episodes_this_iter: 20
  episodes_total: 20
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 4240.323
    load_time_ms: 150.942
    num_steps_sampled: 10000
    num_steps_trained: 10000
    rl_0:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.4182323217391968
      kl: 0.0007666427409276366
      policy_loss: -0.0021987531799823046
      total_loss: 25.61863136291504
      vf_explained_var: 0.1952669322490692
      vf_loss: 25.620677947998047
    rl_1:
      cur_kl_coeff: 0.20000000298023224
      cur_lr: 4.999999873689376e-05
      entropy: 1.418394923210144
      kl: 0.0013116004411131144
      policy_loss: -0.0018925844924524426
      to

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=17258], 120 s, 5 iter, 50000 ts, 101 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-35-05
  done: false
  episode_len_mean: 402.25
  episode_reward_max: 280.2998255191442
  episode_reward_mean: 111.64199685597043
  episode_reward_min: -158.02126673190355
  episodes_this_iter: 31
  episodes_total: 142
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 3375.932
    load_time_ms: 27.201
    num_steps_sampled: 60000
    num_steps_trained: 60000
    rl_0:
      cur_kl_coeff: 0.0062500000931322575
      cur_lr: 4.999999873689376e-05
      entropy: 1.4206793308258057
      kl: 0.0014311131089925766
      policy_loss: -0.0011552408104762435
      total

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=17258], 238 s, 10 iter, 100000 ts, 161 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-37-04
  done: false
  episode_len_mean: 271.36
  episode_reward_max: 356.6029616233184
  episode_reward_mean: 134.44522911801468
  episode_reward_min: -163.74955624133113
  episodes_this_iter: 41
  episodes_total: 319
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 3205.89
    load_time_ms: 2.648
    num_steps_sampled: 110000
    num_steps_trained: 110000
    rl_0:
      cur_kl_coeff: 0.00019531250291038305
      cur_lr: 4.999999873689376e-05
      entropy: 1.4184283018112183
      kl: 0.0057281265035271645
      policy_loss: -0.0021758894436061382
      to

...

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.4/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=17258], 713 s, 30 iter, 300000 ts, 312 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-44-59
  done: false
  episode_len_mean: 156.47
  episode_reward_max: 351.430631415661
  episode_reward_mean: 312.5771981519858
  episode_reward_min: 279.096225199232
  episodes_this_iter: 64
  episodes_total: 1424
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 3210.682
    load_time_ms: 2.612
    num_steps_sampled: 310000
    num_steps_trained: 310000
    rl_0:
      cur_kl_coeff: 7.450580707946131e-10
      cur_lr: 4.999999873689376e-05
      entropy: 1.314957618713379
      kl: 0.009836667217314243
      policy_loss: -0.002595038153231144
      total_los

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=17258], 829 s, 35 iter, 350000 ts, 315 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-46-56
  done: false
  episode_len_mean: 151.0
  episode_reward_max: 370.7561129057823
  episode_reward_mean: 324.9705379721828
  episode_reward_min: 287.85112534766967
  episodes_this_iter: 66
  episodes_total: 1751
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 3190.467
    load_time_ms: 2.536
    num_steps_sampled: 360000
    num_steps_trained: 360000
    rl_0:
      cur_kl_coeff: 4.6566129424663316e-11
      cur_lr: 4.999999873689376e-05
      entropy: 1.2764943838119507
      kl: 0.009800616651773453
      policy_loss: -0.0019548204727470875
      tota

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.5/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=17258], 945 s, 40 iter, 400000 ts, 326 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-48-52
  done: false
  episode_len_mean: 141.49
  episode_reward_max: 359.6224120422741
  episode_reward_mean: 324.5467151450176
  episode_reward_min: 289.76580675781986
  episodes_this_iter: 72
  episodes_total: 2094
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 3138.641
    load_time_ms: 2.302
    num_steps_sampled: 410000
    num_steps_trained: 410000
    rl_0:
      cur_kl_coeff: 2.9103830890414573e-12
      cur_lr: 4.999999873689376e-05
      entropy: 1.202426552772522
      kl: 0.006498439237475395
      policy_loss: -0.0019121519289910793
      tota

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=17258], 1061 s, 45 iter, 450000 ts, 331 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-50-48
  done: false
  episode_len_mean: 139.92
  episode_reward_max: 366.46097880827205
  episode_reward_mean: 329.7576528585229
  episode_reward_min: 287.98646653706663
  episodes_this_iter: 70
  episodes_total: 2454
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 3093.157
    load_time_ms: 2.211
    num_steps_sampled: 460000
    num_steps_trained: 460000
    rl_0:
      cur_kl_coeff: 9.094947153254554e-14
      cur_lr: 4.999999873689376e-05
      entropy: 1.1413443088531494
      kl: 0.022095046937465668
      policy_loss: -0.004346325062215328
      tot

== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/3 CPUs, 0/1 GPUs
Memory usage on this node: 9.6/16.4 GB
Result logdir: /home/thorsten/ray_results/IntersectionExample
RUNNING trials:
 - PPO_MultiAgentIntersectionEnv-v0_0:	RUNNING [pid=17258], 1178 s, 50 iter, 500000 ts, 330 rew

Result for PPO_MultiAgentIntersectionEnv-v0_0:
  custom_metrics: {}
  date: 2019-03-16_10-52-45
  done: false
  episode_len_mean: 136.42
  episode_reward_max: 372.22948262587283
  episode_reward_mean: 324.1759006789613
  episode_reward_min: -141.63079371102415
  episodes_this_iter: 73
  episodes_total: 2819
  experiment_id: 24c603b7188b4f0a80a63654cfc9e16b
  hostname: Gandalf
  info:
    grad_time_ms: 3110.017
    load_time_ms: 2.314
    num_steps_sampled: 510000
    num_steps_trained: 510000
    rl_0:
      cur_kl_coeff: 2.2737367883136385e-14
      cur_lr: 4.999999873689376e-05
      entropy: 1.0990521907806396
      kl: 0.007127183489501476
      policy_loss: -0.0026886085979640484
      